<a href="https://colab.research.google.com/github/componavt/wd_book/blob/master/programming_tasks/natural_disasters/Vuleq%20Connect/EqVulConnections.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import folium
import csv
import numpy as np
from geopy.distance import geodesic
from scipy.spatial import KDTree

!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/Vuleq%20Connect/query%20vul.csv
!wget https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/Vuleq%20Connect/query%20eq.csv
m = folium.Map()
Buff_list1 = []
Buff_list2 = []
line_between_objects1 = []
line_between_objects2 = []
repeat_check1 = 0
repeat_check2 = 0
repeat_check11 = 0
repeat_check22 = 0

# Opening a CSV-file and processing it
with open("query vul.csv", encoding='utf-8', newline='') as csvfile:
    reader1 = csv.DictReader(csvfile, delimiter=";")
    for row in reader1:
        # Puy Pariou;Point(2.971484 45.796824) -> popup;point(Buff_list1)
		    # Editing the original coordinates
        popup = row['volcanoLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        Lat = cords.split()
        Buff_list1.extend([float(Lat[0]), float(Lat[1])]) # Adding coordinates to buffer
        # Coordinate processing
        cor = tuple(Buff_list1)
        Buff_list1.clear()
        if (repeat_check1 == cor[0] and repeat_check2 == cor[1]):
            continue
        line_between_objects1.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Volcano', color="red").add_to(
            m)
        repeat_check1 = cor[0]
        repeat_check2 = cor[1]
# The same function is only for earthquakes CVS-file
with open("query eq.csv", encoding='utf-8', newline='') as csvfile:
    reader2 = csv.DictReader(csvfile, delimiter=";")
    for row in reader2:
        popup = row['earthquakeLabel']
        cords = row['location'].replace("Point(", "").replace(")", "")
        Lat = cords.split()
        Buff_list2.extend([float(Lat[0]), float(Lat[1])])
        cor = tuple(Buff_list2)
        Buff_list2.clear()
        if (repeat_check11 == cor[0] and repeat_check22 == cor[1]):
            continue
        line_between_objects2.append((cor[1], cor[0]))
        folium.Circle(radius=500, location=[cor[1], cor[0]], popup=popup, tooltip='Earthquake',
                      color="black").add_to(m)
        repeat_check11 = cor[0]
        repeat_check22 = cor[1]

# Drawing a line between two coordinates using K-Demension Trees
	# The used algorithm is described in "Maneewongvatana and Mount" 1999.
	# The general idea is that the  is a binary tree, each of whose nodes represents an axis-aligned hyperrectangle.
	# Each node specifies an axis and splits the set of points based on whether their coordinate along that axis is greater than or less than a particular value.
tree1 = KDTree(line_between_objects1) # Creating KDTree with the values of our coordinates
dist = 63 # Minimal distance for creating a line (63 the maximum distance at which an earthquake affects a volcano)
closest_points = tree1.query(line_between_objects2, k=1, distance_upper_bound=dist)[1]

closest_pairs_check_array = []
for i in range(len(line_between_objects1)):
    if closest_points[i] != len(line_between_objects1):
        eq_location = line_between_objects2[i]
        volcano_location = line_between_objects1[closest_points[i]]
        distance = geodesic(eq_location, volcano_location).kilometers
        if distance <= dist:
            closest_pairs_check_array.append((eq_location, volcano_location, distance))
#Drawing lines
for pair in closest_pairs_check_array:
    folium.PolyLine([pair[0], pair[1]], color="purple", weight=1, opacity=1).add_to(m)
# Saving the map
m

--2024-04-01 07:09:52--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/Vuleq%20Connect/query%20vul.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 76165 (74K) [text/plain]
Saving to: ‘query vul.csv’

query vul.csv       100%[===================>]  74.38K  --.-KB/s    in 0.01s   

2024-04-01 07:09:53 (5.80 MB/s) - ‘query vul.csv’ saved [76165/76165]

--2024-04-01 07:09:53--  https://raw.githubusercontent.com/componavt/wd_book/master/programming_tasks/natural_disasters/Vuleq%20Connect/query%20eq.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443..